# Pipeline de experimentos PLN

Este notebook é dedicado a criar uma estrutura de pipeline que será utilizada para exemplificar PLN na disciplina ACH2197 - Análise de Redes Sociais

## 1. Estruturação dos dados

Primeiro, vamos importar o conjunto de dados. O conjunto de dados foi extraído de factck.br.

Moreno, João; Bressan, Graça. FACTCK.BR: A New Dataset to Study Fake News. In: ANAIS DO SIMPÓSIO BRASILEIRO DE SISTEMAS MULTIMÍDIA E WEB (WEBMEDIA), 25. , 2019, Rio de Janeiro. Porto Alegre: Sociedade Brasileira de Computação, 2019. p. 525-527.

In [ ]:
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')

import pandas as pd
dados = pd.read_csv('https://raw.githubusercontent.com/digiampietri/basesDeDados/main/factck_br_VF.csv', sep=',', decimal = ',', encoding = 'ISO-8859-1')
dados

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


URL  \
0     https://apublica.org/2017/10/truco-dados-falso...   
1     https://piaui.folha.uol.com.br/lupa/2018/11/22...   
2     https://aosfatos.org/noticias/trump-nao-public...   
3     https://piaui.folha.uol.com.br/lupa/2019/03/11...   
4     https://piaui.folha.uol.com.br/lupa/2019/05/29...   
...                                                 ...   
1047  https://piaui.folha.uol.com.br/lupa/2018/11/22...   
1048  https://aosfatos.org/noticias/nao-e-miriam-lei...   
1049  https://piaui.folha.uol.com.br/lupa/2019/06/21...   
1050  https://aosfatos.org/noticias/jovem-seminu-em-...   
1051  https://piaui.folha.uol.com.br/lupa/2019/04/11...   

                                Author   datePublished  \
0                   https:apublica.org      2017-10-27   
1     https:piaui.folha.uol.com.brlupa  22/11/18 18:21   
2               https:www.aosfatos.org      2018-10-08   
3     https:piaui.folha.uol.com.brlupa  11/03/19 20:30   
4     https:piaui.folha.uol.com.brlupa  29/05/19 19:25   
...                                ...             ...   
1047  https:piaui.folha.uol.com.brlupa  22/11/18 14:56   
1048            https:www.aosfatos.org      2019-07-22   
1049  https:piaui.folha.uol.com.brlupa  21/06/19 07:01   
1050            https:www.aosfatos.org      2019-04-08   
1051  https:piaui.folha.uol.com.brlupa  11/04/19 18:46   

                                          claimReviewed  \
0      baixa a taxa de solução de homicídios no Bras...   
1      bonito ver expoentes mundiais mostrando admir...   
2      engraçado ver a Mídia Brasileira de Fake News...   
3      graças aos soldados, e não aos sacerdotes, qu...   
4        isso aí Messi, sempre fui teu fã e não é a toa   
...                                                 ...   
1047  Vocês conhecem Luiz Martins Bom, esse lixo pet...   
1048  Vos apresento a funcionária protegida pela Glo...   
1049  Vulcão Sinabung entra em erupção na Indonésia ...   
1050  Zeca TchuTchuca [Zeca Dirceu] no auge de sua m...   
1051  Zeca TchuTchuca no auge de sua militância enqu...   

                                             reviewBody  \
0     Na justificativa do projeto do Estatuto do Arm...   
1                                                 Empty   
2      FALSO um tweet de Donald Trump no qual ele ap...   
3                                                 Empty   
4                                                 Empty   
...                                                 ...   
1047                                              Empty   
1048  Uma foto de um treinamento de defesa contra as...   
1049                                              Empty   
1050  O deputado federal Zeca Dirceu PT-PR não é o h...   
1051                                              Empty   

                                                  title  ratingValue  \
0     Dados falsos e omissões marcam Estatuto do Arm...            1   
1     #Verificamos:  falsa foto de Paul McCartney co...            4   
2     Trump não publicou tweet em apoio a Bolsonaro ...            1   
3     #Verificamos: Não é de Obama discurso que asso...            4   
4     #Verificamos:  montagem foto de Messi mostrand...            4   
...                                                 ...          ...   
1047  #Verificamos:  falso que deputado alvo da Oper...            4   
1048  Não é Miriam Leitão quem segura fuzil ao lado ...            1   
1049  #Verificamos: Vídeo não mostra erupção vulcâni...            4   
1050  Jovem seminu em foto da Parada LGBTQ de Atenas...            1   
1051  #Verificamos: Jovem seminu em manifestação não...            4   

      bestRating alternativeName  
0              8           FALSO  
1              6           FALSO  
2              5           FALSO  
3              6           FALSO  
4              6           FALSO  
...          ...             ...  
1047           6           FALSO  
1048           5           FALSO  
1049           6           FALSO  
1050         

Agora, vamos definir as variáveis de interesse (ou seja, a variável texto e a categoria que será prevista). Além disso, vamos utilizar o *Counter* para avaliar se há desbalanceamento entre as classes.

In [ ]:
from collections import Counter

X = dados['claimReviewed']
y = dados['alternativeName']

Counter(y)

Counter({'FALSO': 933, 'VERDADEIRO': 119})

Por fim, vamos dividir o conjunto de dados em duas partições: a de treinamento e a de teste. Isso será feito utilizando o comando *stratify* para que sejam mantidas as mesmas proporções entre as classes no conjunto de treinamento e de teste.

In [ ]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=123, stratify=y)

Counter(y_test)

Counter({'FALSO': 187, 'VERDADEIRO': 24})

## 2. Criação de modelos

Agora, vamos criar os modelos que serão testados na última etapa. Primeiro, vamos importar as bibliotecas que utilizaremos:

In [ ]:
# Pipelines
from sklearn.pipeline import Pipeline

# Engenharia de features
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_selection import SelectKBest, chi2
from sklearn.preprocessing import MinMaxScaler

# Modelos
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.naive_bayes import MultinomialNB

from sklearn import svm
#from nltk import bigrams

# Métricas
from sklearn.metrics import f1_score, precision_score, recall_score, accuracy_score, confusion_matrix

Agora, vamos utilizar o Grid Search CV para criar os modelos com os melhores hiperparâmetros. 

OBS.: O pipeline para o teste dos modelos possui uma etapa de pré-processamento, que também pode impactar (muito) no desempenho de cada modelo e, consequentemente, na escolha dos hiperparâmetros. Isso é uma falha no pipeline que eu ainda preciso pensar em como melhorar.

OBS2.: O código fica comentado porque, no caso de um "Run all" acidental, ele demora um bocado para rodar.

In [ ]:
from unicodedata import normalize

minhaStopList = [normalize('NFKD', n).encode('ASCII', 'ignore').decode('ASCII') for n in stopwords.words('portuguese')]
minhaStopList.append('ii')


In [ ]:
baseline = DummyClassifier(strategy='most_frequent', random_state = 100, constant = None)
reglog = LogisticRegression(class_weight='balanced', max_iter=2000, solver='liblinear', penalty='l2', C=1.3225)
mlp = MLPClassifier(activation='relu', max_iter=2000)
NB = MultinomialNB()

SVM = svm.SVC(kernel='poly', C = 1, gamma=1)

## 3. Comparação dos modelos

Agora, vamos criar um pipeline de pipelines para comparar diferentes combinações de modelos e pré-processamentos diferentes. Abaixo, crio uma lista com todas as combinações que quero testar.

OBS.: É importante dar um nome bom para cada uma das etapas; isso vai ajudar a identificar o modelo em questão na fase de comparações.

In [ ]:
# modelos1: conjunto de modelos que não usam seleção de atributos
modelos1 = [Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('dummy', baseline)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('NB', NB)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('NB', NB)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('relog', reglog)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('NB', NB)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('NB', NB)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('NB', NB)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('NB', NB)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('NB', NB)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('NB', NB)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('relog', reglog)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('relog', reglog)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('relog', reglog)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('relog', reglog)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('mlp', mlp)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('mlp', mlp)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('mlp', mlp)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('mlp', mlp)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('SVM', SVM)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('SVM', SVM)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('SVM', SVM)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('SVM', SVM)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('SVM', SVM)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('SVM', SVM)]),
           ]

# modelos2: conjunto de modelos que usam seleção de atributos com a função SelectKBest
atributos  = 300
modelos2 = [Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('dummy', baseline)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('reglog', reglog)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('reglog', reglog)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('NB', NB)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('KBest', SelectKBest(chi2, k=atributos)),
                              ('SVM', SVM)]),
           ]

# modelos3: conjunto de modelos que utilizam redução de dimensionalidade usando Análise de Componentes Principais (PCA)
modelos3 = [Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('pca', TruncatedSVD(atributos)),
                              ('dummy', baseline)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('bag-of-words', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList)),
                              ('pca', TruncatedSVD(atributos)),
                              ('reglog', reglog)]),
           Pipeline(steps=[('tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,)),
                              ('pca', TruncatedSVD(atributos)),
                              ('reglog', reglog)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)), ('Normalizing',MinMaxScaler()),
                              ('NB', NB)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('relog', reglog)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('mlp', mlp)]),
           Pipeline(steps=[('bigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('uni-bi-trigram', CountVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('bigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(2,2))),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(3,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           Pipeline(steps=[('uni-bi-trigram tf-idf', TfidfVectorizer(strip_accents='ascii', lowercase=True, stop_words=minhaStopList,ngram_range=(1,3))),
                              ('pca', TruncatedSVD(atributos)),
                              ('SVM', SVM)]),
           ]

# Cada bloco a seguir avalia um conjunto de modelos
Os modelos são avaliados considerando validação cruzada utilizando o conjunto de treinamento.

# Modelos que não utilizam nenhuma abordagem de seleção de atributos/redução de dimensionalidade.

In [ ]:
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold 

kf = StratifiedKFold(n_splits=3, random_state = 123, shuffle = True)

testados = modelos1

for m in testados:
  print([i for i,j in m.steps], '\tf1_macro\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='f1_macro').mean(), 3))
  print([i for i,j in m.steps], '\taccuracy\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='accuracy').mean(), 3))
  print([i for i,j in m.steps], '\troc_auc\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='roc_auc').mean(), 3))

['bag-of-words', 'dummy'] 	f1_macro	 0.47
['bag-of-words', 'dummy'] 	accuracy	 0.887
['bag-of-words', 'dummy'] 	roc_auc	 0.5
['bag-of-words', 'mlp'] 	f1_macro	 0.52
['bag-of-words', 'mlp'] 	accuracy	 0.873
['bag-of-words', 'mlp'] 	roc_auc	 0.683
['tf-idf', 'mlp'] 	f1_macro	 0.526
['tf-idf', 'mlp'] 	accuracy	 0.868
['tf-idf', 'mlp'] 	roc_auc	 0.699
['bag-of-words', 'NB'] 	f1_macro	 0.553
['bag-of-words', 'NB'] 	accuracy	 0.885
['bag-of-words', 'NB'] 	roc_auc	 0.699
['tf-idf', 'NB'] 	f1_macro	 0.47
['tf-idf', 'NB'] 	accuracy	 0.887
['tf-idf', 'NB'] 	roc_auc	 0.704
['bag-of-words', 'SVM'] 	f1_macro	 0.468
['bag-of-words', 'SVM'] 	accuracy	 0.88
['bag-of-words', 'SVM'] 	roc_auc	 0.689
['tf-idf', 'SVM'] 	f1_macro	 0.47
['tf-idf', 'SVM'] 	accuracy	 0.887
['tf-idf', 'SVM'] 	roc_auc	 0.707
['bag-of-words', 'relog'] 	f1_macro	 0.576
['bag-of-words', 'relog'] 	accuracy	 0.87
['bag-of-words', 'relog'] 	roc_auc	 0.722
['tf-idf', 'relog'] 	f1_macro	 0.606
['tf-idf', 'relog'] 	accuracy	 0.874
['tf-i

# Modelos que utilizam seleção de atributos (utilizando a função SelectKBest).

In [ ]:
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold 

kf = StratifiedKFold(n_splits=3, random_state = 123, shuffle = True)

testados = modelos2

for m in testados:
  print([i for i,j in m.steps], '\tf1_macro\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='f1_macro').mean(), 3))
  print([i for i,j in m.steps], '\taccuracy\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='accuracy').mean(), 3))
  print([i for i,j in m.steps], '\troc_auc\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='roc_auc').mean(), 3))

['bag-of-words', 'KBest', 'dummy'] 	f1_macro	 0.47
['bag-of-words', 'KBest', 'dummy'] 	accuracy	 0.887
['bag-of-words', 'KBest', 'dummy'] 	roc_auc	 0.5
['bag-of-words', 'KBest', 'mlp'] 	f1_macro	 0.526
['bag-of-words', 'KBest', 'mlp'] 	accuracy	 0.874
['bag-of-words', 'KBest', 'mlp'] 	roc_auc	 0.575
['tf-idf', 'KBest', 'mlp'] 	f1_macro	 0.511
['tf-idf', 'KBest', 'mlp'] 	accuracy	 0.878
['tf-idf', 'KBest', 'mlp'] 	roc_auc	 0.622
['bag-of-words', 'KBest', 'NB'] 	f1_macro	 0.501
['bag-of-words', 'KBest', 'NB'] 	accuracy	 0.891
['bag-of-words', 'KBest', 'NB'] 	roc_auc	 0.569
['tf-idf', 'KBest', 'NB'] 	f1_macro	 0.47
['tf-idf', 'KBest', 'NB'] 	accuracy	 0.887
['tf-idf', 'KBest', 'NB'] 	roc_auc	 0.437
['bag-of-words', 'KBest', 'SVM'] 	f1_macro	 0.498
['bag-of-words', 'KBest', 'SVM'] 	accuracy	 0.886
['bag-of-words', 'KBest', 'SVM'] 	roc_auc	 0.575
['tf-idf', 'KBest', 'SVM'] 	f1_macro	 0.47
['tf-idf', 'KBest', 'SVM'] 	accuracy	 0.887
['tf-idf', 'KBest', 'SVM'] 	roc_auc	 0.63
['bag-of-words', 

# Modelos que utilizam redução de dimensionalidade usando Análise de Componentes Principais (PCA)

In [ ]:
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import StratifiedKFold 

kf = StratifiedKFold(n_splits=3, random_state = 123, shuffle = True)

testados = modelos3

for m in testados:
  print([i for i,j in m.steps], '\tf1_macro\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='f1_macro').mean(), 3))
  print([i for i,j in m.steps], '\taccuracy\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='accuracy').mean(), 3))
  print([i for i,j in m.steps], '\troc_auc\t', round(cross_val_score(m, x_train, y_train, cv=kf, scoring='roc_auc').mean(), 3))

['bag-of-words', 'pca', 'dummy'] 	f1_macro	 0.47
['bag-of-words', 'pca', 'dummy'] 	accuracy	 0.887
['bag-of-words', 'pca', 'dummy'] 	roc_auc	 0.5
['bag-of-words', 'pca', 'mlp'] 	f1_macro	 0.51
['bag-of-words', 'pca', 'mlp'] 	accuracy	 0.873
['bag-of-words', 'pca', 'mlp'] 	roc_auc	 0.715
['tf-idf', 'pca', 'mlp'] 	f1_macro	 0.504
['tf-idf', 'pca', 'mlp'] 	accuracy	 0.883
['tf-idf', 'pca', 'mlp'] 	roc_auc	 0.718
['bag-of-words', 'pca', 'Normalizing', 'NB'] 	f1_macro	 0.47
['bag-of-words', 'pca', 'Normalizing', 'NB'] 	accuracy	 0.887
['bag-of-words', 'pca', 'Normalizing', 'NB'] 	roc_auc	 0.671
['tf-idf', 'pca', 'Normalizing', 'NB'] 	f1_macro	 0.47
['tf-idf', 'pca', 'Normalizing', 'NB'] 	accuracy	 0.887
['tf-idf', 'pca', 'Normalizing', 'NB'] 	roc_auc	 0.707
['bag-of-words', 'pca', 'SVM'] 	f1_macro	 0.472
['bag-of-words', 'pca', 'SVM'] 	accuracy	 0.866
['bag-of-words', 'pca', 'SVM'] 	roc_auc	 0.596
['tf-idf', 'pca', 'SVM'] 	f1_macro	 0.47
['tf-idf', 'pca', 'SVM'] 	accuracy	 0.887
['tf-idf', 

Os diferentes modelos foram avaliados com validação cruzada (usando apenas o conjunto de treinamento). O melhor "deve" ser o selecionado e seu desempenho deverá ser avaliado com o conjunto de teste.

## 4. Teste do modelo escolhido

Testa-se o modelo escolhido (teoricamente o que obteve o melhor desempenho). O modelo é treinado com todo o conjunto de treinamento e testado com o conjunto de teste.

In [ ]:
from sklearn import metrics # Métricas para avaliação da classificação

modelos1[2].fit(x_train, y_train)

preds = modelos1[2].predict(x_test) ### escolha um modelo para verificar seu desemepnho no conjunto de teste
report=metrics.classification_report(y_test,preds)
print(report)


              precision    recall  f1-score   support

       FALSO       0.91      0.97      0.94       187
  VERDADEIRO       0.50      0.25      0.33        24

    accuracy                           0.89       211
   macro avg       0.70      0.61      0.64       211
weighted avg       0.86      0.89      0.87       211



Pipeline de experimentos adaptado de notebook desenvolvido pela ex-aluna Laís Carraro.